# Jupyter Notebook for Coursera Capstone Final Project

## Analysis of opening an Italian Restaurant in Sheffield

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)


## Introduction: Business Problem <a name="introduction"></a>

In this capstone project I will try to find an optimal location for a Italian restaurant in Sheffield, UK. Sheffield is a very different type of city from Berlin. The analysis and parameters take this into account.

Since there are lots of restaurants in Sheffield I will try to detect **locations that are not already crowded with restaurants**. I am also particularly interested in **areas with no Italian restaurants in vicinity**. I would also prefer locations **as close to city center as possible**, assuming that first two conditions are met.

I will generate a list of few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

Based on definition of the problem, factors that will influence our decission are:
* number of existing restaurants in the neighborhood (any type of restaurant)
* number of and distance to Italian restaurants in the neighborhood, if any
* distance of neighborhood from city center

I will use regularly spaced grid of locations, centered around city center, to define the neighborhoods.

Following data sources will be needed to extract/generate the required information:
* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **Google Maps API reverse geocoding**
* number of restaurants and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of Sheffield center will be obtained using **Google Maps API geocoding** of well known Sheffield location (Peace Gardens)

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 12x12 killometers centered around Sheffield city center.

Let's first find the latitude & longitude of Sheffield city center, using specific, well known address and Google Maps geocoding API.

#### Initialise a few things first

In [2]:
import pandas as pd
import numpy as np
import json
import requests
from sklearn.cluster import KMeans
import matplotlib.cm as cm
import matplotlib.colors as colors
import folium

In [3]:
# Load credentials from JSON file to ensure that credentials are not available on a public GitHub

secrets = json.load(open('secrets.json'))
CLIENT_ID = secrets['CLIENT_ID']
CLIENT_SECRET = secrets['CLIENT_SECRET']
VERSION = secrets['VERSION']
google_api_key = secrets['Google_key']

In [4]:
import requests

def get_coordinates(api_key, address, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&address={}'.format(api_key, address)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        geographical_data = results[0]['geometry']['location'] # get geographical coordinates
        lat = geographical_data['lat']
        lon = geographical_data['lng']
        return [lat, lon]
    except:
        return [None, None]
    
address = 'Peace Gardens, Sheffield, United Kingdom'

sheffield_center = get_coordinates(google_api_key, address)
# berlin_center = [52.519441, 13.403935]
print('Coordinate of {}: {}'.format(address, sheffield_center))

Coordinate of Peace Gardens, Sheffield, United Kingdom: [53.37993609999999, -1.4697722]


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~6km from the Peace Gardens. Our neighborhoods will be defined as circular areas with a radius of 500 meters, so our neighborhood centers will be 100 meters apart.

To accurately calculate distances I need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

*Note:* This is a larger distance than in the Berlin scenario as Sheffield is not as densly packed

In [48]:
#!pip install shapely
import shapely.geometry

#!pip install pyproj
import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Sheffield center longitude={}, latitude={}'.format(sheffield_center[1], sheffield_center[0]))
x, y = lonlat_to_xy(sheffield_center[1], sheffield_center[0])
print('Sheffield center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Sheffield center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Sheffield center longitude=-1.4697722, latitude=53.37993609999999
Sheffield center UTM X=-591032.8135016575, Y=6041897.584603281
Sheffield center longitude=-1.4697722000000015, latitude=53.37993609999998


Now I will create a **hexagonal grid of cells**: I will offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [51]:
sheffield_center_x, sheffield_center_y = lonlat_to_xy(sheffield_center[1], sheffield_center[0]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = sheffield_center_x - 10000
x_step = 1000
y_min = sheffield_center_y - 10000 - (int(21/k)*k*1000 - 20000)/2
y_step = 1000 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 500 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(sheffield_center_x, sheffield_center_y, x, y)
        if (distance_from_center <= 10001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

364 candidate neighborhood centers generated.


Now to visualize the data collected have so far: city center location and candidate neighborhood centers:

In [54]:
map_sheffield = folium.Map(location=sheffield_center, zoom_start=11)
folium.Marker(sheffield_center, popup='Peace Gardens').add_to(map_sheffield)
for lat, lon in zip(latitudes, longitudes):
    #folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_berlin) 
    folium.Circle([lat, lon], radius=500, color='blue', fill=False).add_to(map_sheffield)
    #folium.Marker([lat, lon]).add_to(map_sheffield)
map_sheffield

I now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~6km from the Peace Gardens. 

I will use Google Maps API to get approximate addresses of those locations.

In [55]:
def get_address(api_key, latitude, longitude, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&latlng={},{}'.format(api_key, latitude, longitude)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        address = results[0]['formatted_address']
        return address
    except:
        return None

addr = get_address(google_api_key, sheffield_center[0], sheffield_center[1])
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(sheffield_center[0], sheffield_center[1], addr))

Reverse geocoding check
-----------------------
Address of [53.37993609999999, -1.4697722] is: Peace Gardens, 50 Pinstone St, Sheffield City Centre, Sheffield S1 2HH, UK


In [56]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(google_api_key, lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', UK', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [57]:
addresses[150:170]

['25 Hemmingway Cl, Treeton, Rotherham S60 5RY',
 '2 St Helens Cl, Treeton, Rotherham S60 5QQ',
 'Pleasley Rd, Aughton, Sheffield S26 3XL',
 'Unnamed Road, Sheffield S10',
 'Fulwood Ln, Sheffield S10 4QH',
 'Foxhall Ln, Sheffield S10 4QA',
 'New Carr House, Quiet Ln, Sheffield S10 4GN',
 '24 Mayfield Heights, Sheffield S10 3TT',
 '2 Whiteley Wood Rd, Sheffield S11 7FE',
 '44 Peveril Rd, Sheffield S11 7AP',
 '2 Eastwood Rd, Sharrow, Sheffield S11 8QE',
 '129 Cemetery Rd, Highfield, Sheffield S11 8FN',
 'The Anvil, 109 Clough Rd, Highfield, Sheffield S2 4TB',
 '83 Norfolk Rd, Sheffield S2 2SZ',
 '126 Southend Rd, Sheffield S2 5FT',
 '23 Greenwood Cres, Sheffield S9 4HE',
 '132 Handsworth Ave, Darnall, Sheffield S9 4BW',
 '115 Willow Dr, Darnall, Sheffield S9 4AS',
 'Advanced Manufacturing Park, Whittle Way, Catcliffe, Rotherham S60 5BL',
 'Orgreave Rd, Catcliffe, Rotherham S60 5TX']

Looking good. I will now place all this into a Pandas dataframe.

In [12]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address   Latitude  Longitude  \
0  231 Greenhill Ave, Meadowhead, Sheffield S8 7TJ  53.326987  -1.476166   
1           81 Norton Ln, Norton, Sheffield S8 8GX  53.328214  -1.467528   
2                  A6102, Norton, Sheffield S8 8JA  53.329440  -1.458888   
3                      A6102, Norton, Sheffield S8  53.330665  -1.450248   
4                   Lightwood Ln, Sheffield S8 8BG  53.331890  -1.441607   
5                 1 Lightwood Ln, Sheffield S8 8BG  53.333114  -1.432966   
6                25 Stoneley Dr, Sheffield S12 3JS  53.334338  -1.424324   
7      13 Old Park Rd, Greenhill, Sheffield S8 7DS  53.329625  -1.490900   
8   103 Greenhill Ave, Greenhill, Sheffield S8 7TG  53.330852  -1.482261   
9    39 Little Norton Ln, Norton, Sheffield S8 8GA  53.332079  -1.473622   

               X             Y  Distance from center  
0 -592832.813502  6.036182e+06           5992.495307  
1 -592232.813502  6.036182e+06           5840.376700  
2 -591632.813502  6.036182e+06           5747.173218  
3 -591032.813502  6.036182e+06           5715.767665  
4 -590432.813502  6.036182e+06           5747.173218  
5 -589832.813502  6.036182e+06           5840.376700  
6 -589232.813502  6.036182e+06           5992.495307  
7 -593732.813502  6.036701e+06           5855.766389  
8 -593132.813502  6.036701e+06           5604.462508  
9 -592532.813502  6.036701e+06           5408.326913

...and let's now save/persist this data into local file

In [58]:
df_locations.to_pickle('./sheffield_locations.pkl')

### Foursquare
Now that I have our location candidates, I will use Foursquare API to get info on restaurants in each neighborhood.

I am interested in venues in 'food' category, but only those that are proper restaurants - coffe shops, pizza places, bakeries etc. are not direct competitors so I don't am not interested in these. So I will include in out list only venues that have 'restaurant' in category name, and I will make sure to detect and include all the subcategories of specific 'Italian restaurant' category, as I need info on Italian restaurants in the neighborhood.

### Note that Fourquare credentials were loaded from the external file

In [62]:
# Category IDs corresponding to Italian restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

italian_restaurant_categories = ['4bf58dd8d48988d110941735','55a5a1ebe4b013909087cbb6','55a5a1ebe4b013909087cb7c',
                                 '55a5a1ebe4b013909087cba7','55a5a1ebe4b013909087cba1','55a5a1ebe4b013909087cba4',
                                 '55a5a1ebe4b013909087cb95','55a5a1ebe4b013909087cb89','55a5a1ebe4b013909087cb9b',
                                 '55a5a1ebe4b013909087cb98','55a5a1ebe4b013909087cbbf','55a5a1ebe4b013909087cb79',
                                 '55a5a1ebe4b013909087cbb0','55a5a1ebe4b013909087cbb3','55a5a1ebe4b013909087cb74',
                                 '55a5a1ebe4b013909087cbaa','55a5a1ebe4b013909087cb83','55a5a1ebe4b013909087cb8c',
                                 '55a5a1ebe4b013909087cb92','55a5a1ebe4b013909087cb8f','55a5a1ebe4b013909087cb86',
                                 '55a5a1ebe4b013909087cbb9','55a5a1ebe4b013909087cb7f','55a5a1ebe4b013909087cbbc',
                                 '55a5a1ebe4b013909087cb9e','55a5a1ebe4b013909087cbc2','55a5a1ebe4b013909087cbad']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=200):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [66]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found italian restaurants

foursquare_client_id = CLIENT_ID
foursquare_client_secret = CLIENT_SECRET
import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    italian_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=700 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, foursquare_client_id, foursquare_client_secret, radius=700, limit=200)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_italian = is_restaurant(venue_categories, specific_filter=italian_restaurant_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_italian, x, y)
                if venue_distance<=500:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_italian:
                    italian_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, italian_restaurants, location_restaurants

# Try to load from local file system in case we did this before
restaurants = {}
italian_restaurants = {}
location_restaurants = []
loaded = False
try:
    with open('sheffield_restaurants_700.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('sheffield_italian_restaurants_700.pkl', 'rb') as f:
        italian_restaurants = pickle.load(f)
    with open('sheffield_location_restaurants_700.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    restaurants, italian_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('sheffield_restaurants_700.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('sheffield_italian_restaurants_700.pkl', 'wb') as f:
        pickle.dump(italian_restaurants, f)
    with open('sheffield_location_restaurants_700.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)
    print('Restaurant data saved.')
        

Restaurant data loaded.


In [67]:
print('Total number of restaurants:', len(restaurants))
print('Total number of Italian restaurants:', len(italian_restaurants))
print('Percentage of Italian restaurants: {:.2f}%'.format(len(italian_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 237
Total number of Italian restaurants: 25
Percentage of Italian restaurants: 10.55%
Average number of restaurants in neighborhood: 0.5439560439560439


In [68]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('53381186498e6c25ed6ef01f', 'Bridge Inn, Ridgeway', 53.30919508247245, -1.3980612723641812, 'United Kingdom', 654, False, -588157.8883899278, 6033011.944731162)
('4d03d68ac2e53704e77eb467', "Kam's Garden", 53.300152, -1.494998, 'Dronfield, Derbyshire, United Kingdom', 622, False, -594771.0212143795, 6033528.392864838)
('4f887c95e4b057e27fa05764', 'Simply Chinese @The Rock', 53.302267144138845, -1.470927431169228, 'Dronfield (Chesterfield Road), United Kingdom', 607, False, -593132.126656228, 6033384.949345293)
('4d4c47dbfe85a1cdcea89bbf', 'Village Fisheries', 53.30144318231036, -1.4684601396706243, 'United Kingdom', 533, False, -592991.2393763328, 6033255.961945955)
('4bd099e3a8b3a5935138645f', 'Little Italy', 53.30581505330447, -1.4744352591948378, 'Dronfield, Derbyshire, United Kingdom', 357, True, -593270.518791602, 6033829.367780338)
('4efb76d40e61a084710df2d5', 'Mint Leaf', 53.30433796417003, -1.4650334084635896, 'Green Lane, Dronfi

In [69]:
print('List of Italian restaurants')
print('---------------------------')
for r in list(italian_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(italian_restaurants))

List of Italian restaurants
---------------------------
('4bd099e3a8b3a5935138645f', 'Little Italy', 53.30581505330447, -1.4744352591948378, 'Dronfield, Derbyshire, United Kingdom', 357, True, -593270.518791602, 6033829.367780338)
('58dff6388cfe546add818548', "Frankie & Benny's", 53.34566364994016, -1.3547123596072197, '27 Drake House Crescent, Waterthorpe, Sheffield, S20 7HT, United Kingdom', 388, True, -584362.6779736886, 6036346.102662303)
('4c9d16338afca093945bf315', 'Kitos', 53.342801495515836, -1.478433609008789, '752 Chesterfield Road, Sheffield, S8 0SE, United Kingdom', 474, True, -592569.7309203085, 6037954.132273033)
('5169a446e4b0726c30d3f16e', 'Pesto', 53.34297826050916, -1.500796318458736, 'United Kingdom', 501, True, -594034.9882929281, 6038322.622239162)
('4edfda597ee531b70ad3988f', 'Marco@milanos', 53.343625677966855, -1.5003203523989976, 'United Kingdom', 539, True, -593986.8062864281, 6038386.2917717835)
('4d5efef8b6b9a1cdf1826951', 'Marco@Milano', 53.34559666435906, 

In [70]:
print('Restaurants around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: 
Restaurants around location 102: 
Restaurants around location 103: Marco@Milano
Restaurants around location 104: Viraaj Indian Restaurant, Canton Wok, Kitos
Restaurants around location 105: 
Restaurants around location 106: 
Restaurants around location 107: Flames Take Away, Sophie Hurst Allotts Kitcherrnn
Restaurants around location 108: Stan's Fish & Chip Shop
Restaurants around location 109: 
Restaurants around location 110: Pejis


In [72]:
map_sheffield = folium.Map(location=sheffield_center, zoom_start=12)
folium.Marker(sheffield_center, popup='Peace Gardens').add_to(map_sheffield)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_italian = res[6]
    color = 'red' if is_italian else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_sheffield)
map_sheffield

Looking good. So now I have all the restaurants in area within few kilometers from the Peace Gardens, and I know which ones are Italian restaurants! I also know which restaurants exactly are in vicinity of every neighborhood candidate center.
This concludes the data gathering phase - I am now ready to use this data for analysis to produce the report on optimal locations for a new Italian restaurant!

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of Sheffield that have low restaurant density, particularly those with low number of Italian restaurants. I will limit our analysis to area ~6km around city center.

In first step I have collected the required **data: location and type (category) of every restaurant within 6km from Sheffield center** (Peace Gardens). I have also **identified Italian restaurants** (according to Foursquare categorization).

Second step in the analysis will be calculation and exploration of '**restaurant density**' across different areas of Berlin - I will use **heatmaps** to identify a few promising areas close to center with low number of restaurants in general (*and* no Italian restaurants in vicinity) and focus our attention on those areas.

In third and final step I will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: I will take into consideration locations with **no more than two restaurants in radius of 500 meters**, and we want locations **without Italian restaurants in radius of 800 meters**. I will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

I will perform some basic explanatory data analysis and derive some additional info from the raw data. First I will count the **number of restaurants in every area candidate**:

In [74]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=500m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=500m: 0.5439560439560439


Address   Latitude  Longitude  \
0  231 Greenhill Ave, Meadowhead, Sheffield S8 7TJ  53.326987  -1.476166   
1           81 Norton Ln, Norton, Sheffield S8 8GX  53.328214  -1.467528   
2                  A6102, Norton, Sheffield S8 8JA  53.329440  -1.458888   
3                      A6102, Norton, Sheffield S8  53.330665  -1.450248   
4                   Lightwood Ln, Sheffield S8 8BG  53.331890  -1.441607   
5                 1 Lightwood Ln, Sheffield S8 8BG  53.333114  -1.432966   
6                25 Stoneley Dr, Sheffield S12 3JS  53.334338  -1.424324   
7      13 Old Park Rd, Greenhill, Sheffield S8 7DS  53.329625  -1.490900   
8   103 Greenhill Ave, Greenhill, Sheffield S8 7TG  53.330852  -1.482261   
9    39 Little Norton Ln, Norton, Sheffield S8 8GA  53.332079  -1.473622   

               X             Y  Distance from center  Restaurants in area  \
0 -592832.813502  6.036182e+06           5992.495307                    0   
1 -592232.813502  6.036182e+06           5840.376700                    0   
2 -591632.813502  6.036182e+06           5747.173218                    0   
3 -591032.813502  6.036182e+06           5715.767665                    0   
4 -590432.813502  6.036182e+06           5747.173218                    0   
5 -589832.813502  6.036182e+06           5840.376700                    0   
6 -589232.813502  6.036182e+06           5992.495307                    0   
7 -593732.813502  6.036701e+06           5855.766389                    0   
8 -593132.813502  6.036701e+06           5604.462508                    1   
9 -592532.813502  6.036701e+06           5408.326913                    1   

   Distance to Italian restaurant  
0                     1411.130005  
1                     1542.919577  
2                     1868.131085  
3                     2306.344875  
4                     2776.241650  
5                     2964.420849  
6                     3084.523868  
7                     1048.902163  
8                      932.931854  
9                      948.511874

OK, now I will calculate the **distance to nearest Italian restaurant from every area candidate center** (not only those within 500m - I want distance to closest one, regardless of how distant it is).

In [75]:
distances_to_italian_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in italian_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_italian_restaurant.append(min_distance)

df_locations['Distance to Italian restaurant'] = distances_to_italian_restaurant

In [33]:
df_locations.head(10)

Address   Latitude  Longitude  \
0  231 Greenhill Ave, Meadowhead, Sheffield S8 7TJ  53.326987  -1.476166   
1           81 Norton Ln, Norton, Sheffield S8 8GX  53.328214  -1.467528   
2                  A6102, Norton, Sheffield S8 8JA  53.329440  -1.458888   
3                      A6102, Norton, Sheffield S8  53.330665  -1.450248   
4                   Lightwood Ln, Sheffield S8 8BG  53.331890  -1.441607   
5                 1 Lightwood Ln, Sheffield S8 8BG  53.333114  -1.432966   
6                25 Stoneley Dr, Sheffield S12 3JS  53.334338  -1.424324   
7      13 Old Park Rd, Greenhill, Sheffield S8 7DS  53.329625  -1.490900   
8   103 Greenhill Ave, Greenhill, Sheffield S8 7TG  53.330852  -1.482261   
9    39 Little Norton Ln, Norton, Sheffield S8 8GA  53.332079  -1.473622   

               X             Y  Distance from center  Restaurants in area  \
0 -592832.813502  6.036182e+06           5992.495307                    1   
1 -592232.813502  6.036182e+06           5840.376700                    1   
2 -591632.813502  6.036182e+06           5747.173218                    0   
3 -591032.813502  6.036182e+06           5715.767665                    0   
4 -590432.813502  6.036182e+06           5747.173218                    0   
5 -589832.813502  6.036182e+06           5840.376700                    0   
6 -589232.813502  6.036182e+06           5992.495307                    0   
7 -593732.813502  6.036701e+06           5855.766389                    1   
8 -593132.813502  6.036701e+06           5604.462508                    1   
9 -592532.813502  6.036701e+06           5408.326913                    1   

   Distance to Italian restaurant  
0                     1411.130005  
1                     1542.919577  
2                     1868.131085  
3                     2306.344875  
4                     2776.241650  
5                     2964.420849  
6                     3084.523868  
7                     1048.902163  
8                      932.931854  
9                      948.511874

In [77]:
print('Average distance to closest Italian restaurant from each area center:', df_locations['Distance to Italian restaurant'].mean())

Average distance to closest Italian restaurant from each area center: 3256.1245566009243


OK, so **on average Italian restaurant can be found within ~500m** from every area center candidate. That's fairly close, so we need to filter our areas carefully!

Let's crete a map showing **heatmap / density of restaurants** and try to extract some meaningfull info from that. Also, let's show **borders of Sheffield boroughs** on our map and a few circles indicating distance of 1km, 5km and 10km from the Peace Gardens.

In [78]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

italian_latlons = [[res[2], res[3]] for res in italian_restaurants.values()]

In [79]:
import json
with open('sheffield.geojson') as geojson_file:
    sheffield_geo = json.load(geojson_file)
    sheffield_geo_features = sheffield_geo['features']
def boroughs_style(feature):
    return { 'color': 'blue', 'fill': False }

In [83]:
from folium import plugins
from folium.plugins import HeatMap

map_sheffield = folium.Map(location=sheffield_center, zoom_start=11)
folium.TileLayer('cartodbpositron').add_to(map_sheffield) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_sheffield)
folium.Marker(sheffield_center).add_to(map_sheffield)
folium.Circle(sheffield_center, radius=1000, fill=False, color='white').add_to(map_sheffield)
folium.Circle(sheffield_center, radius=5000, fill=False, color='white').add_to(map_sheffield)
folium.Circle(sheffield_center, radius=10000, fill=False, color='white').add_to(map_sheffield)
folium.GeoJson(sheffield_geo, style_function=boroughs_style, name='geojson').add_to(map_sheffield)


folium.LayerControl().add_to(map_sheffield)
map_sheffield


There is a high concentration of restaurants in the centre and to the South of the city with fewer in the North.

Now I will look specifically for Italian restaurants and we will look closer to the city centre.

In [87]:
map_sheffield = folium.Map(location=sheffield_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_sheffield) #cartodbpositron cartodbdark_matter
HeatMap(italian_latlons).add_to(map_sheffield)
folium.Marker(sheffield_center).add_to(map_sheffield)
folium.Circle(sheffield_center, radius=1000, fill=False, color='white').add_to(map_sheffield)
folium.Circle(sheffield_center, radius=2000, fill=False, color='white').add_to(map_sheffield)
folium.Circle(sheffield_center, radius=3000, fill=False, color='white').add_to(map_sheffield)
folium.GeoJson(sheffield_geo, style_function=boroughs_style, name='geojson').add_to(map_sheffield)
map_sheffield

This map is not quite sparse, showing few italian restaurants in the city. The areas to the West of the city tend to have larger student populations. Students typically spend more on Italian food so these areas are worth investigating further. We will include the popular student areas of Walkley, Broomhill, Fulwood, Sandygate, Upperthorpe and Encliffe.

Unlike Berlin, there is little tourist interest in Sheffield.

In [99]:
roi_x_min = sheffield_center_x - 5000
roi_y_max = sheffield_center_y +3000
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 2500
roi_center_y = roi_y_max - 2500
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_sheffield = folium.Map(location=roi_center, zoom_start=13)
HeatMap(restaurant_latlons).add_to(map_sheffield)
folium.Marker(sheffield_center).add_to(map_sheffield)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_sheffield)
folium.GeoJson(sheffield_geo, style_function=boroughs_style, name='geojson').add_to(map_sheffield)
map_sheffield

This nicely covers all the pockets of low restaurant density in student areas closest to Sheffield center.

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m appart).

In [100]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

2261 candidate neighborhood centers generated.


OK. I will now calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **500 meters**) and **distance to closest Italian restaurant**.

In [106]:
def count_restaurants_nearby(x, y, restaurants, radius=500):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_italian_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=500)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, italian_restaurants)
    roi_italian_distances.append(distance)
print('done.')



Generating data on location candidates... done.


In [107]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Italian restaurant':roi_italian_distances})

df_roi_locations.head(10)

Latitude  Longitude              X             Y  Restaurants nearby  \
0  53.357478  -1.499675 -593582.813502  6.039898e+06                   0   
1  53.357683  -1.498234 -593482.813502  6.039898e+06                   0   
2  53.357098  -1.507895 -594132.813502  6.039984e+06                   0   
3  53.357303  -1.506454 -594032.813502  6.039984e+06                   0   
4  53.357507  -1.505014 -593932.813502  6.039984e+06                   0   
5  53.357712  -1.503573 -593832.813502  6.039984e+06                   0   
6  53.357917  -1.502132 -593732.813502  6.039984e+06                   0   
7  53.358122  -1.500692 -593632.813502  6.039984e+06                   0   
8  53.358327  -1.499251 -593532.813502  6.039984e+06                   0   
9  53.358532  -1.497811 -593432.813502  6.039984e+06                   0   

   Distance to Italian restaurant  
0                      756.721397  
1                      820.734553  
2                      526.788111  
3                      518.154078  
4                      528.641260  
5                      557.170993  
6                      601.180047  
7                      657.567778  
8                      723.445448  
9                      796.461707

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two restaurants in radius of 500 meters**, and **no Italian restaurants in radius of 1000 meters**.

In [108]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_ita_distance = np.array(df_roi_locations['Distance to Italian restaurant']>=1000)
print('Locations with no Italian restaurants within 1000m:', good_ita_distance.sum())

good_locations = np.logical_and(good_res_count, good_ita_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]



Locations with no more than two restaurants nearby: 1479
Locations with no Italian restaurants within 1000m: 432
Locations with both conditions met: 425


In [115]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_sheffield = folium.Map(location=roi_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_sheffield)
HeatMap(restaurant_latlons).add_to(map_sheffield)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(map_sheffield)
folium.Marker(sheffield_center).add_to(map_sheffield)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_sheffield) 
folium.GeoJson(sheffield_geo, style_function=boroughs_style, name='geojson').add_to(map_sheffield)
map_sheffield

There are a range of possible locations. I will now display these as a heatmap.

In [117]:
map_sheffield = folium.Map(location=roi_center, zoom_start=13)
HeatMap(good_locations, radius=25).add_to(map_sheffield)
folium.Marker(sheffield_center).add_to(map_sheffield)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_sheffield)
folium.GeoJson(sheffield_geo, style_function=boroughs_style, name='geojson').add_to(map_sheffield)
map_sheffield

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* Italian restaurants at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [119]:
from sklearn.cluster import KMeans

number_of_clusters = 14

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_sheffield = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_sheffield)
HeatMap(restaurant_latlons).add_to(map_sheffield)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_sheffield)
folium.Marker(sheffield_center).add_to(map_sheffield)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_sheffield) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_sheffield)
folium.GeoJson(sheffield_geo, style_function=boroughs_style, name='geojson').add_to(map_sheffield)
map_sheffield

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [122]:
map_sheffield = folium.Map(location=roi_center, zoom_start=13)
folium.Marker(sheffield_center).add_to(map_sheffield)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_sheffield)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_sheffield)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_sheffield) 
folium.GeoJson(sheffield_geo, style_function=boroughs_style, name='geojson').add_to(map_sheffield)
map_sheffield

Let's zoom in on candidate areas in **Upperthorpe**:

In [124]:
map_sheffield = folium.Map(location=[53.390985, -1.486256], zoom_start=15)
folium.Marker(sheffield_center).add_to(map_sheffield)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_sheffield) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_sheffield)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_sheffield)
folium.GeoJson(sheffield_geo, style_function=boroughs_style, name='geojson').add_to(map_sheffield)
map_sheffield

...and candidate areas in **Sandygate**:

In [126]:
map_sheffield = folium.Map(location=[53.376851, -1.532753], zoom_start=15)
folium.Marker(sheffield_center).add_to(map_sheffield)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_sheffield) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_sheffield)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_sheffield)
folium.GeoJson(sheffield_geo, style_function=boroughs_style, name='geojson').add_to(map_sheffield)
map_sheffield

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [128]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(google_api_key, lat, lon)
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, sheffield_center_x, sheffield_center_y)
    print('{}{} => {:.1f}km from Peace Gardens'.format(addr, ' '*(50-len(addr)), d/1000))
    

Addresses of centers of areas recommended for further analysis

31 Woodfarm Dr, Sheffield S6 5LW, UK               => 4.3km from Peace Gardens
2 Cross Bedford St, Sheffield S6 3AT, UK           => 1.5km from Peace Gardens
23 Burnt Stones Cl, Sheffield S10 5TS, UK          => 4.7km from Peace Gardens
2 Raven Rd, Nether Edge, Sheffield S7 1SB, UK      => 2.6km from Peace Gardens
Wood Lane, Sheffield S6 5AZ, UK                    => 4.0km from Peace Gardens
80 Hall Park Hill, Sheffield S6 5QU, UK            => 4.6km from Peace Gardens
801 Manchester Rd, Sheffield S10 5SY, UK           => 4.7km from Peace Gardens
34 Addy St, Sheffield S6 3FU, UK                   => 1.6km from Peace Gardens
66 Stumperlowe Cres Rd, Sheffield S10 3PR, UK      => 4.8km from Peace Gardens
Rivelin View, Roscoe Bank, Sheffield S6 5SB, UK    => 4.6km from Peace Gardens
46 Rivelin Park Dr, Sheffield S6 5GG, UK           => 3.8km from Peace Gardens
10 Balaclava Rd, Sheffield S6 3BG, UK              => 1.9km from Pe

This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of restaurants and no Italian restaurants nearby, all zones being fairly close to city center (all less than 4km from the Peace Gardens, and about half of those less than 2km from the Peace Gardens). Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. Most of the zones are located in Upperthorpe and Sandygate boroughs, which we have identified as interesting due to being popular with students, fairly close to city center and well connected by public transport.

In [130]:
map_sheffield = folium.Map(location=roi_center, zoom_start=13)
folium.Circle(sheffield_center, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_sheffield)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_sheffield) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_sheffield)
map_sheffield

## Results and Discussion <a name="results"></a>




Sheffield is a very different city to Berlin. Berlin is a national capital with a large tourist influx. Sheffield does not have the same level of tourism, but it does have a significant student population. Students, on the whole, tend to enjor cheaper restaurants and often enjoy Italian food. We examined the low density areas, making sure to steer clear of farmland as cows and sheep would be unlikely to frequent the restaurant.

Narrowing the areas to those with both the student population and a lack of restaurants I created a list of suitable locations with no two restaurants within 250m and no Italian closer than 400m. 

The result is a list of 15 zones with the best potential areas for a new restaurant. These are outside the city centre to reduce competition with existing restaurants. This list provides a useful starting point for consideration, but other factors would need to be considered when planning a restaurant.
